In [1]:
import pickle
import numpy as np

import pandas as pd
from scipy.stats.stats import pearsonr  
from scipy import stats

from matplotlib import pyplot as plt

import os
os.listdir("../../Data/data")

['PageTimes-2022-12-30.csv',
 'improv_ctrl_2022-12-30.csv',
 'improv_focus_2023-01-06.csv',
 'PageTimes-2023-01-06.csv']

In [2]:
ctrl = pd.read_csv('../../Data/data/improv_ctrl_2022-12-30.csv')
ctrl = ctrl[ctrl['participant.label'].notna()]
ctrl_1 = ctrl[ctrl["player.id_in_group"] == 1]

In [3]:
focus = pd.read_csv('../../Data/data/improv_focus_2023-01-06.csv')
focus = focus[focus['participant.label'].notna()]
focus_1 = focus[focus["player.id_in_group"] == 1]

In [4]:
scores_ctrl = pickle.load(open("scores.pkl", "rb"))
scores_focus = pickle.load(open("scores_focus.pkl", "rb"))

In [5]:
def filter_df_by_story(df, storynum, version='ctrl'):
    if storynum == 1:
        df = df[df["subsession.round_number"] <= 12]
    elif storynum == 2:
        df = df[(df["subsession.round_number"] > 12) & (df["subsession.round_number"] <= 30)]
    elif storynum == 3:
        if version == 'ctrl':
            df = df[(df["subsession.round_number"] > 30) & (df["subsession.round_number"] <= 42)]
        else:
            df = df[(df["subsession.round_number"] > 37) & (df["subsession.round_number"] <= 49)]
    elif storynum ==4:
        if version == 'ctrl':
            df = df[(df["subsession.round_number"] > 42) & (df["subsession.round_number"] <= 60)]
        else:
            df = df[(df["subsession.round_number"] > 49) & (df["subsession.round_number"] <= 67)]
    return df
    

In [6]:
def get_ratings_story(scores_dict, df, version):
    scores_all = np.zeros((33, 4))
    subject_list = list(scores_dict.keys())
    scores = []
    scores_subs = []
    for idx in range(len(subject_list)):
        for storynum in range(1, 5):
            subject = subject_list[idx]
            df = df[df["participant.label"] == subject]
            df = filter_df_by_story(df, storynum, version)
            scores_st = scores_dict[subject][storynum]
            if len(scores_st) == 0:
                continue
            scores_subs.append(np.mean(scores_st))
            scores_all[idx][storynum-1]=np.mean(scores_st)
       
    
    scores_subs = np.array(scores_subs)
    return scores_all

In [7]:
scores_all_ctrl = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")

In [8]:
scores_ctrl_1 = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")
scores_ctrl_2 = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")
scores_ctrl_3 = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")
scores_ctrl_4 = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")
print(np.mean(scores_ctrl_1), np.mean(scores_ctrl_2), np.mean(scores_ctrl_3), np.mean(scores_ctrl_4))
print((np.mean(scores_ctrl_1) + np.mean(scores_ctrl_2))/2, (np.mean(scores_ctrl_3) + np.mean(scores_ctrl_4))/2)

TypeError: get_ratings_story() got an unexpected keyword argument 'storynum'

In [9]:
scores_focus_1 = get_ratings_story(scores_focus, focus_1, storynum=1, version="focus")
scores_focus_2 = get_ratings_story(scores_focus, focus_1, storynum=2, version="focus")
scores_focus_3 = get_ratings_story(scores_focus, focus_1, storynum=3, version="focus")
scores_focus_4 = get_ratings_story(scores_focus, focus_1, storynum=4, version="focus")

print(np.mean(scores_focus_1), np.mean(scores_focus_2), np.mean(scores_focus_3), np.mean(scores_focus_4))
print((np.mean(scores_focus_1) + np.mean(scores_focus_2))/2, (np.mean(scores_focus_3) + np.mean(scores_focus_4))/2)

TypeError: get_ratings_story() got an unexpected keyword argument 'storynum'

In [10]:
scores_all_ctrl = get_ratings_story(scores_ctrl, ctrl_1, version="ctrl")
scores_all_ctrl = scores_all_ctrl[~np.any(scores_all_ctrl == 0, axis=1)]

In [11]:
scores_all_focus = get_ratings_story(scores_focus, focus_1, version="focus")
scores_all_focus = scores_all_focus[~np.any(scores_all_focus == 0, axis=1)]

In [12]:
scores_all_ctrl_unconstr = (scores_all_ctrl[:, 2] - scores_all_ctrl[:, 0])/ scores_all_ctrl[:, 0]
scores_all_focus_unconstr = (scores_all_focus[:, 2] - scores_all_focus[:, 0])/ scores_all_focus[:, 0]
scores_all_ctrl_constr = (scores_all_ctrl[:, 3] - scores_all_ctrl[:, 1])/ scores_all_ctrl[:, 1]
scores_all_focus_constr = (scores_all_focus[:, 3] - scores_all_focus[:, 1]) / scores_all_focus[:, 1]

In [16]:
print(np.std(scores_all_ctrl_unconstr[:27]))
print(np.std(scores_all_focus_unconstr[:27]))

0.21746931452622142
0.22373994089318125


In [17]:
print(np.mean(scores_all_ctrl_constr[:27]))
print(np.mean(scores_all_focus_constr[:27]))

-0.09145590239381571
-0.05745745858289709


In [18]:
stats.ttest_rel(scores_all_ctrl_unconstr[:27], scores_all_focus_unconstr[:27] )

Ttest_relResult(statistic=-1.0818985909089542, pvalue=0.28923033956958716)

In [19]:
stats.ttest_rel(scores_all_ctrl_constr[:27], scores_all_focus_constr[:27] )

Ttest_relResult(statistic=-0.6940327624256746, pvalue=0.4938166263180487)

In [100]:
stats.ttest_rel(np.concatenate([scores_all_ctrl_unconstr[:27], scores_all_ctrl_constr[:27]]), np.concatenate([scores_all_focus_unconstr[:27], scores_all_focus_constr[:27]]))

Ttest_relResult(statistic=-1.2418348758646551, pvalue=0.21976498813623885)

In [104]:
scores_all_ctrl

array([[ 8.08784199,  9.52324009,  8.46849442,  7.44383287],
       [ 8.53550339,  7.67875671, 10.53944111,  6.63652992],
       [ 6.57938337,  9.78148556, 10.60290432,  5.39900589],
       [ 9.32022381,  9.09955406,  8.87256908,  9.77530289],
       [ 8.2860918 ,  8.83192635,  9.05631351,  9.01372242],
       [10.31234741,  9.8283577 ,  8.44051456,  8.50649357],
       [ 5.84170294,  7.61952448,  9.25049114,  8.09639835],
       [10.45465279,  8.8937788 ,  9.60311222,  8.24515629],
       [ 7.28060722,  7.99826813,  6.03701067,  5.49961472],
       [ 7.97744799,  7.48425293,  8.50990295,  7.49372721],
       [ 8.1965971 ,  9.23260975,  9.36251163,  7.1337657 ],
       [ 8.35063839,  8.07862949, 10.41655731,  8.53874874],
       [ 7.94105673,  8.13180447,  7.2300086 ,  7.52382851],
       [ 9.16077614, 10.05864716, 10.93768311,  9.66175175],
       [ 5.92854118,  8.72498989,  7.30851793,  6.95983076],
       [ 7.16395426,  8.43924713,  9.33402538,  7.95268583],
       [ 8.08761883,  8.

In [106]:
np.mean(scores_all_ctrl, axis=1)

array([ 8.38085234,  8.34755778,  8.09069479,  9.26691246,  8.79701352,
        9.27192831,  7.70202923,  9.29917502,  6.70387518,  7.86633277,
        8.48137105,  8.84614348,  7.70667458,  9.95471454,  7.23046994,
        8.22247815,  7.57633758,  8.55515873,  8.44355786,  8.81814337,
        9.00198209,  6.92657125,  7.64471078,  9.40926528, 10.99673605,
        8.02207768,  8.66511524,  9.39670253,  8.43975663])

In [107]:
scores_all_focus

array([[ 9.50195694, 10.00142574,  8.49716854,  8.22990131],
       [ 7.89251089,  7.78302956, 10.30155849,  9.34188366],
       [ 7.76172447, 10.04987621, 10.3500433 ,  7.4048748 ],
       [ 7.53753424,  9.95807934,  9.57731533, 10.04359341],
       [ 6.33187342,  8.61472416,  8.57325268,  7.74403954],
       [ 7.44611359,  8.79557514,  5.6475544 ,  6.88752031],
       [ 7.48966837,  9.19323254, 10.03500843,  6.79220438],
       [ 7.83743715,  8.39379406,  8.00282574,  9.27703762],
       [ 8.80158615,  9.05700397, 10.29778004,  9.08821774],
       [ 5.79366493,  6.32028246,  7.12096977,  7.5306921 ],
       [ 9.84870338, 10.91295147, 10.19025993,  8.44115067],
       [ 8.92573071,  8.88335514,  7.91743851,  4.74775887],
       [ 9.36261749,  8.14206791, 11.26191425,  7.13229942],
       [ 8.06789684,  7.93214798,  7.55236053,  9.50492191],
       [ 7.6997447 ,  6.76431656,  6.68624735,  6.66276884],
       [ 8.59264088,  8.87836933,  8.7116766 ,  7.99592972],
       [ 8.64072704,  9.